# Case Study 1 : Collecting Data from Twitter

# Problem 1: Sampling Twitter Data with Streaming API about a Certain Topic

* Select and include a case topic that you are interested in, for example, "WPI" or "Lady Gaga"
* Use Twitter Streaming API to sample a collection of tweets about this topic in real time. (It would be recommended that the number of tweets should be larger than 200, but smaller than 1 million.
* Store the tweets you downloaded into a local file (txt file or json file) 

In [6]:
import twitter
import io, json
#---------------------------------------------
# Define a Function to Login Twitter API
#---------------------------------------------
def oauth_login():
    #Keys, Tokens generated from the Twitter Developer Account
    
    #CONSUMER_KEY = 'rj72WLqREv6TDVjonzbFE08gl'
    #CONSUMER_SECRET = 'MBeUcV7tqV0k97RhlP99f0Oqtmhn2bTV3jcEvKjyfVnIcYem47' 
    #OAUTH_TOKEN = '1090725632470855680-4De5xxNGIfjbR59JLwk0cAa4eaUJ9p'
    #OAUTH_TOKEN_SECRET = 'qWE5hG2NmNQ0amyYg66ZI9HnceYTD5WtV26jitUeevXxL'
        
    CONSUMER_KEY = '8iDb3PAHLXj470PpEhkEy2F8B'
    CONSUMER_SECRET = 'K3UgeD87rPVveFhLbuKbquaEe3e9KwxFRPbc339LVfcm91RaCv'
    OAUTH_TOKEN = '1090725632470855680-K2o3kPNnWsS3NHZlGsGHjfAaECIc78'
    OAUTH_TOKEN_SECRET = '5Fd9tKy4s2yrWOUa2Oaj0FaC0SCo7pjOC2HFY0uqnaAMe'
    
    auth = twitter.oauth.OAuth(OAUTH_TOKEN, OAUTH_TOKEN_SECRET,
                               CONSUMER_KEY, CONSUMER_SECRET)
    
    twitter_api = twitter.Twitter(auth=auth)
    return twitter_api

#-------------------------------------------------------
#Generic Function to search Tweets using a given Twitter API and search key
#------------------------------------------------------

def twitter_search(twitter_api, q, max_results=1000, **kw):

    search_results = twitter_api.search.tweets(q=q, count=1000, **kw)
    statuses = search_results['statuses']
    
    # Iterate through batches of results by following the cursor until we
    # reach the desired number of results, keeping in mind that OAuth users
    # can "only" make 180 search queries per 15-minute interval.
    
    # Enforce a reasonable limit
    max_results = min(500, max_results)
    
    for _ in range(1000): # 10*100 = 1000
        try:
            next_results = search_results['search_metadata']['next_results']
        except KeyError as e: # No more results when next_results doesn't exist
            break
            
        # Create a dictionary from next_results, which has the following form:
        # ?max_id=313519052523986943&q=NCAA&include_entities=1
        kwargs = dict([ kv.split('=') 
                        for kv in next_results[1:].split("&") ])
        
        search_results = twitter_api.search.tweets(**kwargs)
        statuses += search_results['statuses']
        
        if len(statuses) > max_results: 
            break
            
    return statuses

#------------------------------------------
#JSON Utils
#------------------------------------------
def save_json(filename, data):
    with open('C:/Spring19/DS501_IntrotoDS/Case+Study+Assignment+1/Novak_Djokovic_{0}.json'.format(filename),
              'w', encoding='utf-8') as f:
        json.dump(data, f, ensure_ascii=False)


def load_json(filename):
    with open('C:/Spring19/DS501_IntrotoDS/Case+Study+Assignment+1/Novak_Djokovic_{0}.json'.format(filename), 
              'r', encoding='utf-8') as f:
        return json.load(f)

#----------------------------------------------
# Generate the Twitter API for the login
# Create a Search String for Novak Djokovic (#1 Tennis Player)
# Get 1000 Tweets about the topic and log to json file
# Print the generated json file
#----------------------------------------------

q = 'DjokerNole'

#Generate Twitter API for login
twitter_api = oauth_login()
Collection = twitter_search(twitter_api, q, max_results=1000)

save_json(q, Collection)
results = load_json(q)

print(json.dumps(results, indent=1, ensure_ascii=False))

[
 {
  "created_at": "Tue Feb 12 23:54:44 +0000 2019",
  "id": 1095471294517252099,
  "id_str": "1095471294517252099",
  "text": "RT @novakfoundation: Otvaramo novi vrtić u Mačvanskom Prnjavoru! @jelenadjokovic @DjokerNole 🤓🎥👉 https://t.co/DdzJ6vyCyt",
  "truncated": false,
  "entities": {
   "hashtags": [],
   "symbols": [],
   "user_mentions": [
    {
     "screen_name": "novakfoundation",
     "name": "Novak Djokovic Foundation",
     "id": 1134736518,
     "id_str": "1134736518",
     "indices": [
      3,
      19
     ]
    },
    {
     "screen_name": "jelenadjokovic",
     "name": "Jelena Djokovic",
     "id": 1305692694,
     "id_str": "1305692694",
     "indices": [
      65,
      80
     ]
    },
    {
     "screen_name": "DjokerNole",
     "name": "Novak Djokovic",
     "id": 259925559,
     "id_str": "259925559",
     "indices": [
      81,
      92
     ]
    }
   ],
   "urls": [
    {
     "url": "https://t.co/DdzJ6vyCyt",
     "expanded_url": "http://facebook.com/Novak

# Problem 2: Analyzing Tweets and Tweet Entities with Frequency Analysis

**1. Word Count:** 
* Use the tweets you collected in Problem 1, and compute the frequencies of the words being used in these tweets. 
* Plot a table of the top 30 words with their counts

In [7]:
import re
from itertools import islice

def extract_tweet_entities(statuses):

#Extract the tweet text
    status_texts = [ status['text'] 
                 for status in statuses ]

# Compute a collection of all words from all tweets
    words = [ re.sub('[^A-Za-z0-9 ]+', '', w) 
                  for t in status_texts 
                      for w in t.split()
            ]
#Return the words from the tweets containing 'DJokerNole'
    return words

q = 'DjokerNole'

twitter_api = oauth_login()
statuses = twitter_search(twitter_api, q)
words = extract_tweet_entities(statuses)

# Explore the first 5 items for each...

print(json.dumps(words[0:5], indent=1))

#Send the word to a counter to print out the words
from collections import Counter
for item in [words]:
    c = Counter(item)
    word_count = c.most_common()[:31]
#Print the top 30 words along with the count.
print(word_count) # top 30
print()


[
 "RT",
 "novakfoundation",
 "Otvaramo",
 "novi",
 "vrti"
]
[('', 675), ('DjokerNole', 543), ('RT', 417), ('a', 229), ('of', 223), ('tennis', 211), ('dad', 209), ('Life', 201), ('dadlifeisthebestlife', 200), ('httpstcoZsBfPRx5Zw', 200), ('No', 174), ('is', 104), ('TCurin', 99), ('hitwithme', 93), ('possible', 88), ('Hero', 86), ('arms', 86), ('legs', 86), ('But', 86), ('anything', 86), ('MondayMotivaton', 86), ('httpstcomGk3aIpn3z', 86), ('jelenadjokovic', 51), ('the', 50), ('u', 48), ('novakfoundation', 45), ('I', 43), ('and', 37), ('vrti', 35), ('Prnjavoru', 35), ('you', 34)]



In [8]:
from prettytable import PrettyTable
#Plot a table of the top 30 words with their counts
pt = PrettyTable(field_names=['Word', 'Count']) 
    
for label,count in word_count:
    pt.add_row([label,count])
pt.align[label], pt.align['Count'] = 'l', 'r' # Set column alignment
print(pt)

+----------------------+-------+
|         Word         | Count |
+----------------------+-------+
|                      |   675 |
|      DjokerNole      |   543 |
|          RT          |   417 |
|          a           |   229 |
|          of          |   223 |
|        tennis        |   211 |
|         dad          |   209 |
|         Life         |   201 |
| dadlifeisthebestlife |   200 |
|  httpstcoZsBfPRx5Zw  |   200 |
|          No          |   174 |
|          is          |   104 |
|        TCurin        |    99 |
|      hitwithme       |    93 |
|       possible       |    88 |
|         Hero         |    86 |
|         arms         |    86 |
|         legs         |    86 |
|         But          |    86 |
|       anything       |    86 |
|   MondayMotivaton    |    86 |
|  httpstcomGk3aIpn3z  |    86 |
|    jelenadjokovic    |    51 |
|         the          |    50 |
|          u           |    48 |
|   novakfoundation    |    45 |
|          I           |    43 |
|         

**2. Find the most popular tweets in your collection of tweets**

Please plot a table of the top 10 tweets that are the most popular among your collection, i.e., the tweets with the largest number of retweet counts.


In [9]:
# Install ordered-set 
# python -m pip install ordered-set
import twitter
from ordered_set import OrderedSet

def find_popular_tweets(twitter_api, statuses, retweet_threshold=3):


# Collect the tweets based on the retweet count and make sure they satisfy the retweet threshold limit     
    return [ status
                for status in statuses 
                    if status['retweet_count'] > retweet_threshold ] 
    
# Novak Djokovic is the person of Interest 

q = "DjokerNole"

twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q, max_results=200)
statuses = twitter_search(twitter_api, q)
#Find the most popular tweets
popular_tweets = find_popular_tweets(twitter_api, search_results)
# From the most popular tweets, find the various fields like the Screen name, Tweet ID, Retweet count and the text(tweet)
for tweet in popular_tweets:
    print(tweet['text'], tweet['retweet_count'])
retweets = [
            # Store out a tuple of these three values ...
        (status['retweet_count'], 
        status['retweeted_status']['user']['screen_name'],
        status['retweeted_status']['id'],
        status['text']) 
            
            # ... for each status ...
        for status in statuses 
            
            # ... so long as the status meets this condition.
        if 'retweeted_status' in status.keys()
    ]


retweets_ord_set = OrderedSet(retweets)


from prettytable import PrettyTable
#Plot the top 10 tweets in my collection
pt = PrettyTable(field_names=['Count', 'Screen Name', 'Tweet ID', 'Text'])
[ pt.add_row(row) for row in sorted(retweets_ord_set, reverse=True)[:10] ]
pt.max_width['Text'] = 50
pt.align= 'l'
print(pt)

RT @novakfoundation: Otvaramo novi vrtić u Mačvanskom Prnjavoru! @jelenadjokovic @DjokerNole 🤓🎥👉 https://t.co/DdzJ6vyCyt 57
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @RTS_Sport: .@DjokerNole: Da ponovim igru iz Melburna? Nadam se... &gt;&gt; https://t.co/UsdZpTdNoJ #rtsvesti https://t.co/oUAPtWmiXo 13
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Life of a tennis dad 🤣🤪👍🎾 #dadlifeisthebestlife https://t.co/ZsBfPRx5Zw 606
RT @DjokerNole: Hero 🙌🙏 “No arms. No legs. But anything is possible!” @TCurin @hitwithme #Mo

**3. Find the most popular Tweet Entities in your collection of tweets**

Please plot a table of the top 10 hashtags and top 10 user mentions that are the most popular in your collection of tweets.

In [10]:
def extract_tweet_entities(statuses):

    if len(statuses) == 0:
        return [], [], [], [], []
#From the tweets collected earlier, find the following fields-Screen Name(User mentions) & Hash Tags

    screen_names = [ user_mention['screen_name'] 
                         for status in statuses
                            for user_mention in status['entities']['user_mentions'] ]

    hashtags = [ hashtag['text'] 
                     for status in statuses 
                        for hashtag in status['entities']['hashtags'] ]

    
    return screen_names, hashtags
# The subject of interest is Novak Djokovic

q = 'DjokerNole'

statuses = twitter_search(twitter_api, q)

screen_names, hashtags = extract_tweet_entities(statuses)
    

# Print the top 5 entries of user mentions and hash tags
print(json.dumps(screen_names[0:5], indent=1))
print(json.dumps(hashtags[0:5], indent=1))


[
 "novakfoundation",
 "jelenadjokovic",
 "DjokerNole",
 "DjokerNole",
 "luis021002"
]
[
 "dadlifeisthebestlife",
 "dadlifeisthebestlife",
 "dadlifeisthebestlife",
 "dadlifeisthebestlife",
 "glutenfree"
]


In [11]:
from prettytable import PrettyTable

# Plot the top 10 user mentions and hash tags along with their count

twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q, max_results=50)

for label, data in (('User Mentions', screen_names), 
                    ('Hashtag', hashtags)):
    pt = PrettyTable(field_names=[label, 'Count']) 
    c = Counter(data)
    [ pt.add_row(kv) for kv in c.most_common()[:10] ]
    pt.align[label], pt.align['Count'] = 'l', 'r' # Set column alignment
    print(pt)

+-----------------+-------+
| User Mentions   | Count |
+-----------------+-------+
| DjokerNole      |   562 |
| TCurin          |    99 |
| hitwithme       |    93 |
| jelenadjokovic  |    51 |
| novakfoundation |    45 |
| pmouratoglou    |    26 |
| RTS_Sport       |    17 |
| ATP_Tour        |    17 |
| MihailoTopic    |    14 |
| BasiaID         |     9 |
+-----------------+-------+
+----------------------+-------+
| Hashtag              | Count |
+----------------------+-------+
| dadlifeisthebestlife |   200 |
| MondayMotivaton      |    86 |
| AusOpen              |    15 |
| rtsvesti             |    13 |
| NDF                  |     9 |
| TuesdayThoughts      |     8 |
| भगवान_न_भूलो         |     8 |
| NittoATPFinals       |     4 |
| Djokovic             |     4 |
| glutenfree           |     3 |
+----------------------+-------+


# Problem 3: Getting "All" Friends and "All" Followers of a Popular User in Twitter

* choose a popular twitter user who has many followers, such as "Lady Gaga".
* Get the list of all friends and all followers of the twitter user.
* Plot 20 out of the followers, plot their ID numbers, and their screen names in a table.
* Plot 20 out of the friends (if the user has more than 20 friends), plot their ID numbers, and their screen names in a table.

In [12]:
import sys
import time
from urllib.error import URLError
from http.client import BadStatusLine
import json
import twitter

def make_twitter_request(twitter_api_func, max_errors=10, *args, **kw): 
    
    # A nested helper function that handles common HTTPErrors. Return an updated
    # value for wait_period if the problem is a 500 level error. Block until the
    # rate limit is reset if it's a rate limiting issue (429 error). Returns None
    # for 401 and 404 errors, which requires special handling by the caller.
    def handle_twitter_http_error(e, wait_period=2, sleep_when_rate_limited=True):
    
        if wait_period > 3600: # Seconds
            print('Too many retries. Quitting.', file=sys.stderr)
            raise e
    
        # Adding the response codes for handling error
        
    
        if e.e.code == 401:
            print('Encountered 401 Error (Not Authorized)', file=sys.stderr)
            return None
        elif e.e.code == 404:
            print('Encountered 404 Error (Not Found)', file=sys.stderr)
            return None
        elif e.e.code == 429: 
            print('Encountered 429 Error (Rate Limit Exceeded)', file=sys.stderr)
            if sleep_when_rate_limited:
                print("Retrying in 15 minutes...ZzZ...", file=sys.stderr)
                sys.stderr.flush()
                time.sleep(60*15 + 5)
                print('...ZzZ...Awake now and trying again.', file=sys.stderr)
                return 2
            else:
                raise e # Caller must handle the rate limiting issue
        elif e.e.code in (500, 502, 503, 504):
            print('Encountered {0} Error. Retrying in {1} seconds'\
                  .format(e.e.code, wait_period), file=sys.stderr)
            time.sleep(wait_period)
            wait_period *= 1.5
            return wait_period
        else:
            raise e

    # End of nested helper function
    
    wait_period = 2 
    error_count = 0 
# Execution of twitter_api_func
    while True:
        try:
            return twitter_api_func(*args, **kw)
        except twitter.api.TwitterHTTPError as e:
            error_count = 0 
            wait_period = handle_twitter_http_error(e, wait_period)
            if wait_period is None:
                return
        except URLError as e:
            error_count += 1
            time.sleep(wait_period)
            wait_period *= 1.5
            print("URLError encountered. Continuing.", file=sys.stderr)
            if error_count > max_errors:
                print("Too many consecutive errors...bailing out.", file=sys.stderr)
                raise
        except BadStatusLine as e:
            error_count += 1
            time.sleep(wait_period)
            wait_period *= 1.5
            print("BadStatusLine encountered. Continuing.", file=sys.stderr)
            if error_count > max_errors:
                print("Too many consecutive errors...bailing out.", file=sys.stderr)
                raise



twitter_api = oauth_login()

# Look up twitter for screen_name = DjokerNole

response = make_twitter_request(twitter_api.users.lookup, 
                                screen_name="DjokerNole")

print(json.dumps(response, indent=1))


[
 {
  "id": 259925559,
  "id_str": "259925559",
  "name": "Novak Djokovic",
  "screen_name": "DjokerNole",
  "location": "",
  "description": "Laugh as long as you breathe, love as long as you live!",
  "url": "https://t.co/eAmH8v9Ut8",
  "entities": {
   "url": {
    "urls": [
     {
      "url": "https://t.co/eAmH8v9Ut8",
      "expanded_url": "http://novakdjokovic.com",
      "display_url": "novakdjokovic.com",
      "indices": [
       0,
       23
      ]
     }
    ]
   },
   "description": {
    "urls": []
   }
  },
  "protected": false,
  "followers_count": 8531702,
  "friends_count": 730,
  "listed_count": 16689,
  "created_at": "Wed Mar 02 21:44:22 +0000 2011",
  "favourites_count": 1784,
  "utc_offset": null,
  "time_zone": null,
  "geo_enabled": true,
  "verified": true,
  "statuses_count": 3016,
  "lang": "en",
  "status": {
   "created_at": "Tue Feb 12 16:27:07 +0000 2019",
   "id": 1095358648992198656,
   "id_str": "1095358648992198656",
   "text": "Hey Michael thanks f

In [13]:
import twitter
from functools import partial
from sys import maxsize as maxint

def get_persons_id(twitter_api, screen_name=None, persons_limit=maxint, person_type='followers'):
    
    # Make a twitter request to find the ID's of all the followers of "DjokerNole"
    if(person_type=='followers'):
        get_persons_ids = partial(make_twitter_request, twitter_api.followers.ids,
                                count=5000)
    else:
        get_persons_ids = partial(make_twitter_request, twitter_api.friends.ids,
                                count=5000)

    persons_ids = []
    
    for twitter_api_func, limit, values, label in [
                    [get_persons_ids, persons_limit, persons_ids, person_type]
                ]:
        
        if limit == 0: continue
        
        cursor = -1
        while cursor != 0:
        
            # Use make_twitter_request via the partially bound callable...
            response = twitter_api_func(screen_name=screen_name, cursor=cursor)
            
            if response is not None:
                values += response['ids']
                cursor = response['next_cursor']
                
            print('Fetched {0} total {1} ids for {2}'.format(len(values),\
                  label, (screen_name)),file=sys.stderr)
        
        
            if len(values) >= limit or response is None:
                break

    # Look for the person info with the help of their Personal ID's
    return persons_ids[:persons_limit]

def print_person_Table(persons_ids, person_type):
    person_Info = {}
    for id in (persons_ids[:20]):
        person_Info[id] = make_twitter_request(twitter_api.users.lookup, user_id=id)

    #Print to Table
    from prettytable import PrettyTable
    label1 = person_type + '-ID'
    label2 = person_type + '-ScreenName'
    pt = PrettyTable(field_names=[label1, label2]) 

    for key,val in person_Info.items():
        name = [r['screen_name'] for r in val]
        pt.add_row([key, name.pop()])
    pt.align[label1], pt.align[label2] = 'l', 'r' # Set column alignment
    print(pt)


#Get 20 followers
twitter_api = oauth_login()

followers_ids = get_persons_id(twitter_api, screen_name="DjokerNole", persons_limit=1000, person_type='followers')
print(followers_ids)
print_person_Table(followers_ids, 'Followers')

#Get Follower Screen Names


Fetched 5000 total followers ids for DjokerNole


[1095472421589663744, 1095471415405334528, 1075505329050390528, 944915281742319616, 1069933637301284864, 1095468730379845633, 1095467528317489153, 1095467612136505352, 305145373, 1047317385680568320, 57806997, 1095465192249536517, 446100623, 1095465839707516930, 1095465393886543872, 235690555, 1095465049660030977, 1095464425836863488, 1095460707984920576, 1095294235312562177, 1095462961630593024, 1095456860717572097, 1095461901595750400, 3764906354, 1094700974235635712, 1077333987960545280, 1095460820950093830, 1095459688634826752, 1095460373438836739, 1095458431333478401, 1095456226983448577, 1081339526, 771384465377464320, 1095457000962576384, 1095456121823944704, 1095458829226131458, 1095455528367599618, 1095456964744806400, 1095457890343759873, 1090355290946658304, 1095456980716654593, 1095457375081938944, 1095449726458171393, 1095457298288390144, 1095456639484919809, 1095455332132884481, 1095456103184371712, 30449195, 1095452594695294977, 1095455038674096128, 1095454992285216770, 

+---------------------+----------------------+
| Followers-ID        | Followers-ScreenName |
+---------------------+----------------------+
| 1095472421589663744 |      RosalbaVillan11 |
| 1095471415405334528 |         wubo62652284 |
| 1075505329050390528 |            AmnesyaC9 |
| 944915281742319616  |           BobmarkSrb |
| 1069933637301284864 |      Abutahir_Shafin |
| 1095468730379845633 |              dzenaa1 |
| 1095467528317489153 |       Raquel03949233 |
| 1095467612136505352 |      Danijel67597024 |
| 305145373           |        hopeessential |
| 1047317385680568320 |             toanhino |
| 57806997            |             stucas16 |
| 1095465192249536517 |          BPhenprapha |
| 446100623           |            drakula40 |
| 1095465839707516930 |        Rajay67565207 |
| 1095465393886543872 |      armance87782096 |
| 235690555           |              brazrej |
| 1095465049660030977 |      vxrtoWum17PIbnT |
| 1095464425836863488 |      Qrb5KHkRB7RO8qV |
| 10954607079

In [14]:
#Get 20 Friends
twitter_api = oauth_login()

friends_ids = get_persons_id(twitter_api, screen_name="DjokerNole", persons_limit=20, person_type='friends')
print(followers_ids)
print_person_Table(friends_ids, 'Friends')

Fetched 730 total friends ids for DjokerNole


[1095472421589663744, 1095471415405334528, 1075505329050390528, 944915281742319616, 1069933637301284864, 1095468730379845633, 1095467528317489153, 1095467612136505352, 305145373, 1047317385680568320, 57806997, 1095465192249536517, 446100623, 1095465839707516930, 1095465393886543872, 235690555, 1095465049660030977, 1095464425836863488, 1095460707984920576, 1095294235312562177, 1095462961630593024, 1095456860717572097, 1095461901595750400, 3764906354, 1094700974235635712, 1077333987960545280, 1095460820950093830, 1095459688634826752, 1095460373438836739, 1095458431333478401, 1095456226983448577, 1081339526, 771384465377464320, 1095457000962576384, 1095456121823944704, 1095458829226131458, 1095455528367599618, 1095456964744806400, 1095457890343759873, 1090355290946658304, 1095456980716654593, 1095457375081938944, 1095449726458171393, 1095457298288390144, 1095456639484919809, 1095455332132884481, 1095456103184371712, 30449195, 1095452594695294977, 1095455038674096128, 1095454992285216770, 

+--------------------+--------------------+
| Friends-ID         | Friends-ScreenName |
+--------------------+--------------------+
| 234460808          |        QatarTennis |
| 439909823          |           OKSrbije |
| 4105177214         |           LaverCup |
| 182839067          |    BrainGameTennis |
| 905604214398738433 |           rodlaver |
| 87782384           |    filipkrajinovic |
| 39710060           |       KAndersonATP |
| 759136472          |           FSSrbije |
| 1161840631         |         CoSchedule |
| 3697308501         |       tiebreaktens |
| 57471206           |      marcelomelo83 |
| 104537355          |       olympiacosbc |
| 110398012          |        matteksands |
| 18481641           |            LACOSTE |
| 2182094108         |        PERFECTJJIN |
| 724128384          |          weichen59 |
| 1653548340         |          CaroleSnn |
| 531979487          |    Oliviahsiao0418 |
| 17840799           |          Nic_Leigh |
| 945597554          |     Nadja

* Compute the mutual friends within the two groups, i.e., the users who are in both friend list and follower list, plot their ID numbers and screen names in a table

In [15]:
import numpy as np


twitter_api = oauth_login()

#75000 Followers and 1000 friends are taken to comparetheir mutual relationships.
followers_ids = get_persons_id(twitter_api, screen_name="DjokerNole", persons_limit=75000, person_type='followers')
friends_ids = get_persons_id(twitter_api, screen_name="DjokerNole", persons_limit=1000, person_type='friends')

#For verification only - just include the first followerID into the FriendID. This will avoid null intersection result.  
friends_ids.append(followers_ids[0]);

common = set(followers_ids).intersection(friends_ids)

#Get Intersection of both the lists
cm = np.intersect1d(followers_ids, friends_ids)

print_person_Table(cm, 'Mutual ')


Fetched 5000 total followers ids for DjokerNole
Fetched 10000 total followers ids for DjokerNole
Fetched 15000 total followers ids for DjokerNole
Fetched 20000 total followers ids for DjokerNole
Fetched 25000 total followers ids for DjokerNole
Fetched 30000 total followers ids for DjokerNole
Fetched 35000 total followers ids for DjokerNole
Fetched 40000 total followers ids for DjokerNole
Fetched 45000 total followers ids for DjokerNole
Fetched 50000 total followers ids for DjokerNole
Fetched 55000 total followers ids for DjokerNole
Fetched 60000 total followers ids for DjokerNole
Fetched 65000 total followers ids for DjokerNole
Fetched 70000 total followers ids for DjokerNole
Encountered 429 Error (Rate Limit Exceeded)
Retrying in 15 minutes...ZzZ...
...ZzZ...Awake now and trying again.
Fetched 75000 total followers ids for DjokerNole
Fetched 730 total friends ids for DjokerNole


+---------------------+--------------------+
| Mutual -ID          | Mutual -ScreenName |
+---------------------+--------------------+
| 403523317           |             ZojaKu |
| 1095472421589663744 |    RosalbaVillan11 |
+---------------------+--------------------+


# Problem 4: Business Question 

Run some additional experiments with your data to gain familiarity with the twitter data and twitter API.

* Come up with a business question that Twitter data could help answer.
* Decribe the business case.
* How could Twitter data help a company decide how to spend its resources.

In [24]:
#----------------------------------------------
# Find the 'CONVERSION FACTOR' of Novak Djokovic for Foundation
# i.e, how many of his followers are also interested & following his foundation (for sample size 10000)
# This would determine the reach of his charity/foundation efforts and how much he promotes
# his foundation in his twitter account
#----------------------------------------------
import numpy as np
#Get 20 Followers
twitter_api = oauth_login()

followersIDs_Dj = get_persons_id(twitter_api, screen_name="DjokerNole", persons_limit=10000, person_type='followers')
followersIDs_DjFndn = get_persons_id(twitter_api, screen_name="novakfoundation", persons_limit=60, person_type='followers')

#Get Intersection of both the lists
cm = np.intersect1d(followersIDs_Dj, followersIDs_DjFndn)
save_json('-mutual-djFdn',cm.tolist())  #use tolist() to 'jsonify' the data
print('Converted Followers for Novak: ',len(cm))
print('Percentage Conversion:',len(cm)*100/len(followersIDs_Dj))




Fetched 5000 total followers ids for DjokerNole
Fetched 10000 total followers ids for DjokerNole


Converted Followers for Novak:  16
Percentage Conversion: 0.16


Fetched 5000 total followers ids for novakfoundation


In [25]:
#----------------------------------------------
# Find the 'CONVERSION FACTOR' of Rafael Nadal for his Foundation 
# i.e, how many of his followers are also interested & following his foundation (for sample size 30000)
# This would determine the reach of his charity/foundation efforts and how much he promotes
# his foundation in his twitter account
#----------------------------------------------
import numpy as np
#Get 40 Followers
twitter_api = oauth_login()

followersIDs_Fdx = get_persons_id(twitter_api, screen_name="RafaelNadal", persons_limit=30000, person_type='followers')
followersIDs_FdxFndn = get_persons_id(twitter_api, screen_name="frnadal", persons_limit=40, person_type='followers')

#Get Intersection of both the lists
cm2 = np.intersect1d(followersIDs_Fdx, followersIDs_FdxFndn)
save_json('-mutual-FdxFdn',cm2.tolist())  #use tolist() to 'jsonify' the data
print('Converted Followers for Nadal: ',len(cm2))
print('Percentage Conversion:',len(cm2)*100/len(followersIDs_Fdx))

Fetched 5000 total followers ids for RafaelNadal
Fetched 10000 total followers ids for RafaelNadal
Fetched 15000 total followers ids for RafaelNadal
Fetched 20000 total followers ids for RafaelNadal
Fetched 25000 total followers ids for RafaelNadal
Fetched 30000 total followers ids for RafaelNadal


Converted Followers for Nadal:  18
Percentage Conversion: 0.06


Fetched 5000 total followers ids for frnadal


In [26]:
#----------------------------------------------
# Find the 'CONVERSION FACTOR' of Roger Federer for his Foundation 
# i.e, how many of his followers are also interested & following his foundation (for sample size 20000)
# This would determine the reach of his charity/foundation efforts and how much he promotes
# his foundation in his twitter account
#----------------------------------------------
import numpy as np
#Get 50 Followers
twitter_api = oauth_login()

followersIDs_Fdx = get_persons_id(twitter_api, screen_name="rogerfederer", persons_limit=20000, person_type='followers')
followersIDs_FdxFndn = get_persons_id(twitter_api, screen_name="rogerfedererfdn", persons_limit=50, person_type='followers')

#Get Intersection of both the lists
cm2 = np.intersect1d(followersIDs_Fdx, followersIDs_FdxFndn)
save_json('-mutual-FdxFdn',cm2.tolist())  #use tolist() to 'jsonify' the data
print('Converted Followers for Federer: ',len(cm2))
print('Percentage Conversion:',len(cm2)*100/len(followersIDs_Fdx))

Fetched 5000 total followers ids for rogerfederer
Fetched 10000 total followers ids for rogerfederer
Fetched 15000 total followers ids for rogerfederer
Fetched 20000 total followers ids for rogerfederer


Converted Followers for Federer:  8
Percentage Conversion: 0.04


Fetched 5000 total followers ids for rogerfedererfdn
